In [2]:
import glob
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 500)
import re
from sklearn.feature_extraction.text import TfidfVectorizer
from utils_textMining import *


Loading CKIP transformers model...
Loading Simplified Chinese stopwords...
Loading Traditional Chinese stopwords...


統一規格
- 品牌
- 子品類 (breadcrumb)

In [3]:
tfidf_vectorizer = TfidfVectorizer(analyzer='word', stop_words=stopwords_zhCN)#, max_df=1.0, min_df=0.2)


In [4]:
def get_tfidf_col(df, index_col, kw_col):
    """
    計算 tfidf score 後以 dataframe 格式輸出
    :param df:
    :param kw_col:
    :return:
    """
    tfidfVector = tfidf_vectorizer.fit_transform(df[kw_col].values.tolist())
    # print(word_pool_tfidfVector.shape)
    # print(vectorizer.get_feature_names())
    keyword_tfidf = pd.DataFrame(tfidfVector.toarray(), index=df.index.values.tolist(),
                                 columns=tfidf_vectorizer.get_feature_names()) \
                      .reset_index().rename(columns={'index': index_col})
    return keyword_tfidf


def get_tfidf_score(row, df, kw_col='keywords', prod_col='product_id'):
    try:
        return df[row[kw_col]][row[prod_col]]
    except:
        return 0.0
    
    

In [ ]:
# Amazon
amazon_prod = pd.read_csv('Amazon/AmazonUS-query=(fitness_workout)-productDetail.csv')
amazon_prod.head()

# JD
jd_prod = pd.read_csv('JD/JD-query=健身-productDetail.csv')
jd_prod.head()

# Taobao
taobao_prod = pd.read_csv('Taobao/Taobao-query=健身-productDetail.csv')
taobao_prod.head()

# Momo
momo_prod = pd.read_csv('Momo/Momo-query=健身-productDetail.csv')
momo_prod.head()

# PChome - 缺品牌名(頁面本身就無標示)
pchome_prod = pd.read_csv('PChome/PChome-query=健身-productDetail.csv')
pchome_prod.head()

# Shopee - 資訊無結構，不一定有品牌名及子品類
# 爬商品詳情頁時非常卡&慢
shopee_prod = pd.read_csv('Shopee/Shopee-query=健身-productDetail.csv')
shopee_prod.head()


In [20]:
path_list = glob.glob('octoparse_export/Momo-productDetail-query=母嬰*.csv')
print(path_list)
query_list = ['兒童', '媽咪', '嬰兒', '孕婦', '幼兒', '寶寶']
for i in range(len(path_list)):
    frame = pd.read_csv(path_list[i]).drop_duplicates().reset_index(drop=True)
    frame['query'] = query_list[i]
    if i == 0:
        momo = frame.copy()
    else:
        momo = pd.concat([momo, frame]).drop_duplicates().reset_index(drop=True)

momo


['octoparse_export\\Momo-productDetail-query=母嬰-20210914T120056.csv', 'octoparse_export\\Momo-productDetail-query=母嬰-20210914T145422.csv', 'octoparse_export\\Momo-productDetail-query=母嬰-20210914T175503.csv', 'octoparse_export\\Momo-productDetail-query=母嬰-20210914T181925.csv']


title  \
0      \n          【Oral-B 歐樂B】兒童牙刷Cars(5-7歲)\n      ...   
1      \n          【E-home】YOYO幼幼多功能兒童成長椅-三色可選(學童椅)\n...   
2      \n          【Disney 迪士尼】冰雪奇緣 米奇米妮便攜式彈跳蓋防摔直飲水壺4...   
3      \n          【美國 Plackers派樂絲】兒童果香含氟牙線棒-75入\n   ...   
4      \n          【花王】植萃弱酸洗髮精兒童專用補充包(220ml)\n       ...   
...                                                  ...   
11474  \n          【dr.hold 黛后】全身撫紋緊緻精萃油 X 1(孕媽咪譽最愛的「...   
11475  \n          【英國ALLOYA愛若雅】EC 017 無毒水性指甲油(孕婦安全 藕...   
11476  \n          【恆伸醫療器材】ER-5001洗澡椅 防滑設計衛浴設備 老人孕婦淋浴...   
11477  \n          【Freego】產/孕婦用100%純棉拋棄式內褲6包30入裝(孕婦免...   
11478  \n          【赫而司】新元氣綜合錠全素食維他命60顆*2罐(美國GMP製造進口女...   

                                             description    origin_price  \
0      \n          品號：5349893\n          專為乳齒或恆齒可交替時期...         建議售價69元   
1      \n          品號：8096724\n          雙背採人體工學，提供支撐...     建議售價10,000元   
2      \n          品號：7776539\n          最受喜愛迪士尼動畫電影安...         促銷價519元   
3      \n          品號：9123214\n          兒童牙線均塗有氟化物有雙...        建議售價219元   
4      \n          品號：4351475\n          好沖不易殘留培養小朋友自...        建議售價109元   
...                                                  ...             ...   
11474  \n          品號：9073180\n          添加4大專利的高效專利淡...      市售價1,280元    
11475  \n          品號：3592041\n          無毒指甲油 / 水性指甲...  折扣後價格398元 賣貴通報   
11476  \n          品號：9135224\n          原廠保固一年多段式調整高...      市售價1,250元    
11477  \n          品號：3834077\n          可重複洗滌100%純棉使...        市售價990元    
11478  \n          品號：9170815\n          以天然胡蘿蔔素取代維他命...      市售價2,000元    

                                             sales_price  \
0      \n              \n              促銷價49元 \n     ...   
1      \n              \n              促銷價2,350元 \n  ...   
2      \n              \n              折扣後價格442元 \n  ...   
3      \n              \n              促銷價169元 \n    ...   
4      \n              \n              促銷價99元 \n     ...   
...                                                  ...   
11474                                     折扣後價格553元 賣貴通報   
11475                                     折扣後價格398元 賣貴通報   
11476                                       促銷價903元 賣貴通報   
11477                                       促銷價829元 賣貴通報   
11478                                     促銷價1,600元 賣貴通報   

                                                   brand  \
0                                    品牌名稱\n:\nOral-B 歐樂B   
1                                        品牌名稱\n:\nE-home   
2                                    品牌名稱\n:\nDisney 迪士尼   
3                                  品牌名稱\n:\nPlackers 派樂絲   
4                                        品牌名稱\n:\nKao 花王   
...                                                  ...   
11474                                品牌名稱\n:\ndr.hold 黛后   
11475                                品牌名稱\n:\nALLOYA 愛若雅   
11476                                    品牌名稱\n:\n恆伸醫療器材   
11477  結帳方式:\n                \n                  \n ...   
11478                                       品牌名稱\n:\n赫而司   

                               color  \
0                                NaN   
1                     顏色:灰色藍色粉紅請選擇顏色   
2                       顏色:藍色紫色請選擇顏色   
3                                NaN   
4                                NaN   
...                              ...   
11474                            NaN   
11475                 規格1:藕紫風情請選擇規格1   
11476  尺寸:ER-5001-藍綠色ER-5001-黃色請選擇尺寸   
11477                 規格1:單一規格請選擇規格1   
11478                            NaN   

                                              breadcrumb  \
0      \n\n\n      \n       Home\n       \n         \...   
1      \n\n\n      \n       Home\n       \n         \...   
2      \n\n\n      \n       Home\n       \n         \...   
3      \n\n\n      \n       Home\n       \n          ...   
4      \n\n\n      \n       Home\n       \n         \...   
...                                                  ...   
11474  \n\n\n      \n       Home\n       \n         \...   
11475  \n\n\n 

In [139]:
# 第二波

# 無評分
ec_486 = pd.read_csv('octoparse_export/486-searchResult-20210831T094900.csv')
ec_486.shape
ec_486.head()

mamilove = pd.read_csv('octoparse_export/mamilove-searchResult-20210830T214700.csv')
mamilove.shape
mamilove.head()

# 無評分
freemart = pd.read_csv('octoparse_export/freemart-searchResult-20210830T214700.csv')
freemart.shape
freemart.head()

buy123 = pd.read_csv('octoparse_export/buy123-searchResult-20210830T214700.csv')
buy123.shape
buy123.head()

ihergo = pd.read_csv('octoparse_export/ihergo-searchResult-20210830T214700.csv')
ihergo.shape
ihergo.head()

# 無評分
ec_17life = pd.read_csv('octoparse_export/17life-searchResult-20210830T214700.csv')
ec_17life.shape
ec_17life.head()

shopee = pd.read_csv('octoparse_export/shopee-searchResult-20210903T190700.csv')
shopee.shape
shopee.head()

# (以上沒有特別標類別 直接分詞作為聲量統計 (看到標題放什麼大家喜歡買))

# pcone (有麵包屑也有評分、銷量，當作選品池之一)


100%|██████████████████████████████████████████████████████████████████████████████████| 37/37 [00:06<00:00,  5.53it/s]
C:\ProgramData\Anaconda3\envs\tf22\lib\site-packages\IPython\core\interactiveshell.py:3166: DtypeWarning: Columns (4) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


(731965, 9)

title  \
0              Ystrive Made｜現貨🚚自訂款-Y01蝙蝠袖透膚襯衫3.0版-6色   
1  【CHING'S獨家】超顯瘦彈性極佳中高腰黑褲 長褲 S-2XL 黑釦真拉鍊前後口袋 黑褲 ...   
2                         FREEDA │ 現貨-極細交叉長版運動內衣(四色)   
3  【KOREA MOOS】純色無色差穿搭西褲標準8色西裝長褲 九分褲 西裝褲 西裝褲男 九分 ...   
4  ✿MERCI 附發票✿ FB熱銷🏆升級3.0版 莫代爾帶胸墊T恤 BRA背心 長襯裙 免穿內...   

                                                 url  discount_rate  \
0  https://shopee.tw/Ystrive-Made%EF%BD%9C%E7%8F%...            6.7   
1  https://shopee.tw/%E3%80%90CHING'S%E7%8D%A8%E5...            NaN   
2  https://shopee.tw/FREEDA-%E2%94%82-%E7%8F%BE%E...            NaN   
3  https://shopee.tw/%E3%80%90KOREA-MOOS%E3%80%91...            4.4   
4  https://shopee.tw/%E2%9C%BFMERCI-%E9%99%84%E7%...            NaN   

  origin_price sales_price  sales_num location label             Current_Time  
0         $490         329  已售出 6,992   桃園市桃園區   NaN  2021-08-31 00:06:42.326  
1          NaN         299   已售出 6.6萬   臺北市南港區  蝦皮優選  2021-08-31 00:06:42.380  
2          NaN         680  已售出 7,772   新北市新莊區  蝦皮優選  2021-08-31 00:06:42.426  
3         $799         350   已售出 2.4萬   臺中市太平區   NaN  2021-08-31 00:06:42.477  
4          NaN         139   已售出 1.3萬   新北市樹林區   NaN  2021-08-31 00:06:42.527

In [894]:
amazon_prod = pd.read_csv('Amazon/AmazonUS-query=(fitness_workout)-productDetail.csv')
amazon_prod.columns = [col.lower() for col in amazon_prod.columns]
amazon_prod = amazon_prod[amazon_prod['title']!='undefined']
amazon_prod['inventory'] = amazon_prod['inventory'].fillna('In Stock.')
# amazon_prod.head()
amazon_prod = amazon_prod.astype(str)
amazon_prod = amazon_prod.assign(
    brand=amazon_prod.brand.apply(lambda x: x.replace('Visit the', '').replace('Store', '').replace('Brand:', '').strip()), 
    subcategory=amazon_prod.best_sellers_rank.apply(
        lambda x: np.unique([char.strip() for char in re.split('\n|\(|\)| in |\xa0', x.strip()) if (char != '') and (not any(c in char for c in ['#',';','Top ']))]).tolist()), 
    bullet_points=amazon_prod.bullet_points.apply(lambda x: ';'.join([string for string 
              in re.split('\xa0|\n|This fits your| Make sure this fits|by entering your model number.|About this item', x) 
              if not any(s == string for s in ['', '.'])])),
    star_rating=amazon_prod.star_rating.apply(lambda x: x.replace(' out of 5 stars', '')),
    price_floor=amazon_prod.price.apply(lambda x: x.split('-')[0].strip().replace('$', '') if len(x.split('-')) == 2 else x.replace('$', '')),
    price_ceil=amazon_prod.price.apply(lambda x: x.split('-')[1].strip().replace('$', '') if len(x.split('-')) == 2 else x.replace('$', '')),
    number_of_reviews=amazon_prod.number_of_reviews.apply(lambda x: x.replace(' global rating', '').replace('s', '').replace(',', '')),
    number_of_answered_questions=amazon_prod.number_of_answered_questions.apply(lambda x: x.replace(' answered questions', '')),
    inventory=amazon_prod.inventory.apply(lambda x: re.split('\n| - ', x)[0]),
    seller=amazon_prod.seller.apply(lambda x: x[:int(len(x)/2)] if x != 'nan' else x)
)
for col in ['price_floor', 'price_ceil', 'star_rating', 'number_of_reviews', 'number_of_answered_questions']:
    amazon_prod[col] = pd.to_numeric(amazon_prod[col], errors='coerce')
    if col in ['star_rating', 'number_of_reviews', 'number_of_answered_questions']:
        amazon_prod[col] = amazon_prod[col].fillna(0.0)
    
    
amazon_prod['inventory'] = amazon_prod['inventory'].apply(lambda x: 'In Stock' if ('out' not in x) and ('soon' not in x) and ('tock' in x) else 'Currently Unavailable')
amazon_prod = amazon_prod[['title','brand','subcategory','bullet_points','price_floor','price_ceil','star_rating',
                           'number_of_reviews','number_of_answered_questions','inventory','seller']]
amazon_prod.columns = ['title','brand','subcategory','description','price_floor','price_ceil','review_score',
                           'review_num','answered_question_num','inventory_status','seller']
amazon_prod.to_csv('Amazon/Preprocessed-AmazonUS-query=(fitness_workout)-productDetail.csv', index=False)
amazon_prod.head()
amazon_prod.info()



title     brand  \
0  Wyze Smart Scale, Body Fat Scale, Heart Rate M...      WYZE   
1  Scales for Body Weight, Bveiugn Digital Bathro...   posture   
2  BCAN 40" Foldable Mini Trampoline, Fitness Reb...      BCAN   
3  Ballista Bow: Workout Bow - Portable Home Gym ...  BALLISTA   
4  Fitbit Inspire 2 Health & Fitness Tracker with...    Fitbit   

                                         subcategory  \
0  [Body Fat Monitors, Digital Bathroom Scales, H...   
1      [Digital Bathroom Scales, Health & Household]   
2           [Fitness Trampolines, Sports & Outdoors]   
3  [Exercise & Fitness Equipment, Sports & Outdoors]   
4   [Activity & Fitness Trackers, Sports & Outdoors]   

                                         description  price_floor  price_ceil  \
0  【Complete Body Composition Analysis 】 Wyze Sca...          NaN         NaN   
1  Keep Tracking Changes with a Glance - Always k...        27.99       27.99   
2  【2021 Material Upgraded】The second-generation ...        99.99       99.99   
3  ☑️ FULL BODY HOME GYM - The Ballista Bow is a ...       249.00      249.00   
4  Earn Active Zone Minutes as you progress towar...        88.95       88.95   

   review_score  review_num  answered_question_num       inventory_status  \
0           4.7     15735.0                  276.0  Currently Unavailable   
1           4.7     20053.0                  251.0               In Stock   
2           4.5      4753.0                  160.0               In Stock   
3           4.3       127.0                    6.0               In Stock   
4           4.5     31122.0                  668.0               In Stock   

           seller  
0             nan  
1  Posture Direct  
2            BCAN  
3             nan  
4    Dave Parkers

<class 'pandas.core.frame.DataFrame'>
Int64Index: 133 entries, 0 to 137
Data columns (total 11 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   title                  133 non-null    object 
 1   brand                  133 non-null    object 
 2   subcategory            133 non-null    object 
 3   description            133 non-null    object 
 4   price_floor            95 non-null     float64
 5   price_ceil             95 non-null     float64
 6   review_score           133 non-null    float64
 7   review_num             133 non-null    float64
 8   answered_question_num  133 non-null    float64
 9   inventory_status       133 non-null    object 
 10  seller                 133 non-null    object 
dtypes: float64(5), object(6)
memory usage: 12.5+ KB


Empty DataFrame
Columns: [title, brand, subcategory, description, price_floor, price_ceil, review_score, review_num, answered_question_num, inventory_status, seller]
Index: []

In [16]:
# JD
def product_desc_cleansing(x):
    desc = list()
    for spec in x.split(';'):
        if (len(spec.split('：')) == 2) and (spec.split('：')[0] not in ['品牌','商品名称','商品编号','商品毛重','商品产地','货号','店铺','国产/进口','重量']):
            for item in re.split('/|／|（|）|，', spec.split('：')[1]):
                desc.append(item)
    
    return ' '.join(desc)
            
jd_prod = pd.read_csv('JD/Preprocessed-JD-query=健身-productDetail.csv')
# jd_prod.columns = ['title','platform','url','seller','sales_price','spec','desc','category','style','ps','current_time',
#                    'origin_price','review_num','review_score']
# jd_prod = jd_prod[jd_prod['title'].notnull()]
# for col in ['style','ps']:
#     jd_prod[col] = jd_prod[col].fillna(' ')

# jd_prod['origin_price'] = jd_prod['origin_price'].fillna(jd_prod['sales_price'])
# jd_prod.isnull().sum()
jd_prod = jd_prod.assign(
    brand=jd_prod.desc.apply(lambda x: x.split(';')[0].replace('品牌： ', '')),
    desc=jd_prod.desc.apply(lambda x: product_desc_cleansing(x)),
    spec=jd_prod.spec.apply(lambda x: ''.join([s for s in x if s not in stopwords_zhTW])),
#     category=jd_prod.category.apply(lambda x: ' '.join(x.split('>')[:-2])),
    style=jd_prod['style'].apply(lambda x: ' '.join([opt for opt in x.split(';') if (opt != '') and (opt != 'nan')])),
    review_score = jd_prod.review_score.apply(lambda x: x.replace('%', ''))
)
for col in ['style']:
    jd_prod[col] = jd_prod[col].fillna(' ')
    
for col in ['origin_price','sales_price','review_num','review_score']:
    jd_prod[col] = pd.to_numeric(jd_prod[col], errors='coerce')

jd_prod['origin_price'] = jd_prod['origin_price'].fillna(jd_prod['sales_price'])
jd_prod['style'] = jd_prod['style'].apply(lambda x: '' if len(x) == 0 else x)
# jd_prod = jd_prod[['title','category','desc','origin_price','sales_price','seller','review_num','review_score','style']]
jd_prod.to_csv('JD/Preprocessed-JD-query=健身-productDetail.csv', index=False)
jd_prod.info()
jd_prod.head()



In [988]:
taobao_prod = pd.read_csv('Taobao/Taobao-query=健身-productDetail.csv')
for col in ['tags', 'specifications','suggest_keywords']:
    taobao_prod[col] = taobao_prod[col].fillna('None')
    
taobao_prod.isnull().sum()
taobao_prod = taobao_prod.assign(
    review_num=taobao_prod.review_num.apply(lambda x: x.replace('評價', '').replace('+', '').replace('萬', '0000')),
    sales_num=taobao_prod.sales_num.apply(lambda x: x.replace('已售', '').replace('件', '').replace('+', '').replace('萬', '0000')),
    price_floor=taobao_prod.price.apply(lambda x: x.split('-')[0].strip().replace('¥', '') if len(x.split('-')) == 2 else x.replace('¥', '')),
    price_ceil=taobao_prod.price.apply(lambda x: x.split('-')[1].strip().replace('¥', '') if len(x.split('-')) == 2 else x.replace('¥', '')),
    subcategory=taobao_prod.breadcrumb.apply(lambda x: ' '.join([char for char in re.split('\n| > ', x) if char.strip() != ''][1:])),
    tags=taobao_prod.tags.apply(lambda x: ' '.join([char.strip()[1:] for char in re.split('\n|\(|\)|[0-9]+', x) if char.strip() != ''])),
    specifications=taobao_prod.specifications.apply(
        lambda x: {item.split(': ')[0]: item.split(': ')[1] if (len(item.split(': ')) == 2) else 'None'
                   for item in [char.strip() for char in x.split('\n') if char.strip() != '']}),
    suggest_keywords=taobao_prod.suggest_keywords.apply(lambda x: ' '.join([char.strip() for char in x.split('\n') if char.strip() != '']))
)
for col in ['review_num','sales_num','price_floor','price_ceil']:
    taobao_prod[col] = pd.to_numeric(taobao_prod[col], errors='coerce')

taobao_prod['brand'] = taobao_prod['specifications'].apply(lambda x: x['品牌'] if '品牌' in x.keys() else 'None')
for col in ['subcategory','suggest_keywords']:
    taobao_prod[col] = taobao_prod[col].apply(lambda x: 'None' if len(x) == 0 else x)
    
taobao_prod = taobao_prod[['title','subcategory','brand','review_num','sales_num','price_floor','price_ceil',
                           'specifications','tags','suggest_keywords']]
taobao_prod.to_csv('Taobao/Preprocessed-Taobao-query=健身-productDetail.csv', index=False)
taobao_prod.info()
taobao_prod.head()


title               0
review_num          0
sales_num           0
price               0
breadcrumb          0
image_url           0
tags                0
specifications      0
suggest_keywords    0
dtype: int64

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 812 entries, 0 to 811
Data columns (total 10 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   title             812 non-null    object 
 1   subcategory       812 non-null    object 
 2   brand             812 non-null    object 
 3   review_num        812 non-null    int64  
 4   sales_num         812 non-null    int64  
 5   price_floor       812 non-null    float64
 6   price_ceil        812 non-null    float64
 7   specifications    812 non-null    object 
 8   tags              812 non-null    object 
 9   suggest_keywords  812 non-null    object 
dtypes: float64(2), int64(2), object(6)
memory usage: 63.6+ KB


title                        subcategory  \
0         健腹輪腹肌懶人健身器減腹瘦肚子神器家用健身器材自動回彈健腹器  運動/瑜伽/健身/球迷用品 踏步機/中小型健身器材 健腹輪/健腹輪   
1        奧克斯專業級筋膜槍肌肉放鬆電動按摩器儀頸膜搶健身上肌膜機492                               None   
2         湯臣倍健增肌粉純乳清蛋白質粉健身瘦人增肌增重健肌粉男肌肉營養          保健滋補醫藥器械 人羣健康 0-18歲 厭食/挑食   
3  Nutrend諾特蘭德純乳清蛋白質粉增健肌粉健身男瘦人增重2.5磅whey          保健滋補醫藥器械 人羣健康 0-18歲 厭食/挑食   
4         筋膜槍肌肉放鬆按摩器電動家用頸膜機儀健身勁膜搶mini肌膜儀                               None   

            brand  review_num  sales_num  price_floor  price_ceil  \
0             施耐德         100       6500        289.0       289.0   
1         AUX/奧克斯         100       9000        398.0       398.0   
2  BY－HEALTH/湯臣倍健         100      20000        265.0       348.0   
3            諾特蘭德         100       7500        218.0       259.0   
4             福客萊         100      40000        129.0       188.0   

                                      specifications  \
0  {'品牌': '施耐德', '圖案': '其他', '顏色分類': '智能健腹輪-灰【實時數...   
1  {'品牌': 'AUX/奧克斯', '圖案': '其他', '顏色分類': '【聯賽款-綠】...   
2  {'生產日期': '2020年06月01日 至 2020年06月30日', '品牌': 'B...   
3  {'生產日期': '2020年07月14日 至 2021年06月09日', '品牌': '諾...   
4  {'品牌': '福客萊', '材質': 'ABS', '圖案': '其他', '顏色分類':...   

                                   tags  \
0  新手特別適合 很有減肥效果 組裝挺容易 真心不打滑 承重力更強 質量很差   
1   檔位可調節 肌肉不痠痛 很瘦小腿 震動讓人舒服 電源線齊全 商家不給力   
2        喝起來胃口 不甜 吸收性好很多 減脂 沒疲憊感 肌肉沒啥變化   
3    沒有副作用 沖泡起來方便 可以減肥 送人滿意 改善明顯 草莓味真難喝   
4             力度 材質好漂亮 力道很 頸椎 不容易發熱 少配件   

                                    suggest_keywords  
0  練肚子健身器收腹多功能仰臥板 腹肌健身器懶人收腹機 健腹器懶人收腹機仰臥起坐健身器 美腰機收...  
1  理療筋膜槍 筋膜槍按摩 筋膜槍按摩槍 電動筋膜槍 專業級筋膜槍 肌肉筋膜槍專業 女筋膜槍 筋...  
2  蛋白增肌粉健身瘦人增重湯臣倍健 乳清蛋白增肌粉健身減脂 乳清蛋白質粉增肌健身 乳清蛋白增肌粉...  
3  粉乳清蛋白質粉 乳清蛋白質粉 蛋白乳清蛋白質粉 高鈣乳清蛋白質粉 eb蛋白乳清蛋白質粉 速溶...  
4  泡沫軸肌肉放鬆瘦腿按摩器套裝 瑜伽柱泡沫軸肌肉放鬆滾軸按摩器 筋膜槍肌肉放鬆器按摩槍健身電動...

In [990]:
momo_prod = pd.read_csv('Momo/Momo-query=健身-productDetail.csv')
for col in ['color','breadcrumb']:
    momo_prod[col] = momo_prod[col].fillna('None')
    
momo_prod = momo_prod.assign(
    description=momo_prod.description.apply(lambda x: ' '.join([string.strip() for string in x.split('\n') if (string.strip() != '') and ('品號' not in string)])), 
    origin_price=momo_prod.origin_price.apply(lambda x: x.replace('\n', '').replace('建議售價', '').replace('促銷價', '').replace('元', '').replace(',', '').replace('賣貴通報', '').strip()),
    sales_price=momo_prod.sales_price.apply(lambda x: x.replace(' ', '').replace('\n', '').replace('折扣後價格', '').replace('建議售價', '').replace('促銷價', '').replace('元', '').replace('賣貴通報', '').replace('下單再折', '').replace(',', '').strip()), 
    brand=momo_prod.brand.apply(lambda x: x.split('\n:\n')[1] if '品牌' in x else 'None'),
    color=momo_prod.color.apply(lambda x: x[3:-5] if x != 'None' else x),
    breadcrumb=momo_prod.breadcrumb.apply(lambda x: ' '.join([char.strip() for char in x.split('\n') if char.strip() != ''][1:]) if x != 'None' else x)
)
for col in ['description']:
    momo_prod[col] = momo_prod[col].apply(lambda x: 'None' if len(x) == 0 else x)
for col in ['origin_price','sales_price']:
    momo_prod[col] = pd.to_numeric(momo_prod[col], errors='coerce')
    
momo_prod.to_csv('Momo/Preprocessed-Momo-query=健身-productDetail.csv', index=False)
momo_prod.info()
momo_prod.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 303 entries, 0 to 302
Data columns (total 7 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   title         303 non-null    object
 1   description   303 non-null    object
 2   origin_price  303 non-null    int64 
 3   sales_price   303 non-null    int64 
 4   brand         303 non-null    object
 5   color         303 non-null    object
 6   breadcrumb    303 non-null    object
dtypes: int64(2), object(5)
memory usage: 16.7+ KB


title  \
0                                     【健身大師】超跑款飛輪健身車   
1  【Future Lab.未來實驗室】URBANFITNESS城市健身組(36kg啞鈴組+健身...   
2                   【健身大師】未來者專利型電動健步機(循環踏步機/坐走機/復健機)   
3                               【健身大師】超越者X型平板無段變速健身車   
4                            【健身大師】窈窕版無段變速織帶健身車-PINK   

                                description  origin_price  sales_price  \
0  專業踏板鋁合金高科技材質..爆汗款式驅動阻力程式設計腳墊可低根據地面水平做調整.         16800         3480   
1    10秒超簡易組裝居家專業健身椅一次鍛練到全身各部位肌群鈦鋼鋁合金打造超級堅固          6000         3999   
2        健步、復健、空中踩踏新機種運動方向正反轉使用3種自動程式控制變化速度         19800         6800   
3     升級扶手型+平板架可調座椅+靠背+扶手+平板架顯示各項資訊面板讓你有效運動          6800         1999   
4               多工顯示面板設計變速採用無段速織帶設計強化下部肌力順練          3280         1980   

               brand color                   breadcrumb  
0               健身大師  時尚黑紅    運動/按摩 健身器材 品牌總覽(A~Z) 健身大師  
1  Future Lab. 未來實驗室  None  運動/按摩 重量訓練器材 本月主打 未來實驗室▼熱銷中  
2               健身大師     黑          運動/按摩 健身器材 有氧健身 踏步機  
3               健身大師  None  運動/按摩 健身器材 本月主打 居家健身↘鏟肉5折up  
4               健身大師     粉    運動/按摩 健身器材 品牌總覽(A~Z) 健身大師

In [991]:
emoji_pattern = re.compile('['
                          u'\U0001F300-\U0001F5FF'  # symbols & pictographs
                          u'\U0001F600-\U0001F64F'  # emoticons
                          u'\U0001F680-\U0001F6FF'  # transport & map symbols
                          u'\U0001F1E0-\U0001F1FF'  # flags (iOS)
                          u'\U00002000-\U00002FFF'  # av-symbol
                           ']+', flags=re.UNICODE)


In [992]:
pchome_prod = pd.read_csv('PChome/PChome-query=健身-productDetail.csv')
pchome_prod = pchome_prod[pchome_prod['title'].notnull()]
pchome_prod['origin_price'] = pchome_prod['origin_price'].fillna(pchome_prod['sales_price'])
for col in ['description', 'specification']:
    pchome_prod[col] = pchome_prod[col].fillna('None')

pchome_prod = pchome_prod.assign(
    title=pchome_prod.title.apply(lambda x: emoji_pattern.sub(r' ', x)), 
    description=pchome_prod.description.apply(lambda x: emoji_pattern.sub(r' ', x).replace('\n', ' ')), 
    specification=pchome_prod.specification.apply(lambda x: emoji_pattern.sub(r' ', x).replace('\n', ' ')), 
    origin_price=pchome_prod.origin_price.apply(lambda x: x.replace('\n', '').replace('網路價', '').replace('建議售價', '').replace('$', '').strip()),
    sales_price=pchome_prod.sales_price.apply(lambda x: x.replace('\n', '').replace('網路價', '').replace('$', '').strip()),
    breadcrumb=pchome_prod.breadcrumb.apply(lambda x: ' '.join([char.strip() for char in emoji_pattern.sub(r' ', x).split('\n') if char.strip() != ''][3:]))
)
for col in ['origin_price','sales_price']:
    pchome_prod[col] = pd.to_numeric(pchome_prod[col])
    
pchome_prod.to_csv('PChome/Preprocess-PChome-query=健身-productDetail.csv', index=False)
pchome_prod.info()
pchome_prod.head()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 1565 entries, 0 to 1564
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   title          1565 non-null   object
 1   description    1565 non-null   object
 2   origin_price   1565 non-null   int64 
 3   sales_price    1565 non-null   int64 
 4   breadcrumb     1565 non-null   object
 5   specification  1565 non-null   object
dtypes: int64(2), object(4)
memory usage: 85.6+ KB


title  \
0   【BEFIT 星品牌】美國磁控飛輪車 SPIN CYCLE (2色) (超靜音健身車 一年保固)   
1   Switch灰黑電力加強版日規主機(保固一年)+健身環+包+貼+充電座+熱門遊戲任選一送隨機特典   
2  超大材積【BLADEZ】302 Lynx Air 2.0-18.5kg 鍊條鑄鐵飛輪健身車\...   
3               Nintendo Switch《健身環大冒險》中文版 +《精選遊戲》x1   
4  【多功能環狀訓練彈力帶】500*50*0.7mm 乳膠 彈力帶 拉力帶 彈力繩 健身 瑜珈 ...   

                                         description  origin_price  \
0                 超靜音磁控阻力系統   專業級鋁鐵合一飛輪   360度平板/手機架         14800   
1  現貨供應 原裝進口日規主機(支援繁體中文介面) 主機經銷商保固一年 熱門運動遊戲 健身環 最...         16452   
2    高效傳動最強感受   弧形底座車體剛性結構提升   高穩定性承重120KG   全車台製...         20800   
3    您目前所參考的商品為保護級   台灣公司貨   收錄超過40種健身招式    遊戲支援繁...          4440   
4    多種用處       針對不同部位進行訓練        瑜珈輔助       復健伸展...          1200   

   sales_price               breadcrumb  \
0         9999            健身 ．BEFIT 星品牌   
1        14999  電 玩 / 遊 戲 Switch 主機&超值組   
2        13999            健身 ．BLADEZ健身館   
3         3880         電 玩 / 遊 戲 NS 健身環   
4          359            健身 ．彈力帶 / 拉力繩   

                                       specification  
0  適用於初次使用者以及進階運動愛好者 ，提供您專屬的有氧運動訓練。   專業級鋁鐵合一飛輪  ...  
1  ．Nintendo Switch 電力加強版主機 (日規) ．灰色 Joy-Con 控制器組...  
2  機身尺寸:長115寬65高125公分 機身重量:47KG 最高限重:120KG 顏色:防鏽白...  
3  平　　台：NS 版本發行：任天堂 遊玩人數:1人 發售日期：2019-10-31 製作廠商：...  
4              材質：天然乳膠 尺寸：500*50*0.7mm 阻力值：15LB-20LB

In [993]:
shopee_prod = pd.read_csv('Shopee/Shopee-query=健身-productDetail.csv')    
shopee_prod[['origin_price','sales_price','discount']] = shopee_prod.price.str.split('\n', expand=True)
shopee_prod['sales_price'] = shopee_prod['sales_price'].fillna(shopee_prod['origin_price'])
for col in ['origin_price','sales_price']:
    shopee_prod[col] = shopee_prod[col].apply(lambda x: x.replace('$', '').replace(',', ''))
    
for col in ['spec','avg_rating','review_num','discount']:
    shopee_prod[col] = shopee_prod[col].fillna('None')

shopee_prod = shopee_prod.rename(columns={'avg_rating': 'review_score'})
shopee_prod = shopee_prod.assign(
    title=shopee_prod.title.apply(lambda x: emoji_pattern.sub(r' ', x)), 
    description=shopee_prod.product_desc.apply(lambda x: emoji_pattern.sub(r' ', x).replace('\n', ' ').strip()), 
    spec=shopee_prod.spec.apply(lambda x: ' '.join(x.split('\n')) if x != 'None' else x),
    origin_price_floor=shopee_prod.origin_price.apply(lambda x: x.split('-')[0].strip() if (len(x.split('-')) == 2) else x.strip()),
    origin_price_ceil=shopee_prod.origin_price.apply(lambda x: x.split('-')[1].strip() if (len(x.split('-')) == 2) else x.strip()),
    sales_price_floor=shopee_prod.sales_price.apply(lambda x: x.split('-')[0].strip() if (len(x.split('-')) == 2) else x.strip()),
    sales_price_ceil=shopee_prod.sales_price.apply(lambda x: x.split('-')[1].strip() if (len(x.split('-')) == 2) else x.strip()),
    discount=shopee_prod.discount.apply(lambda x: float(x[:-1].strip()) / 10 if x != 'None' else 0.0), 
    review_num=shopee_prod.review_num.apply(lambda x: x.replace(',', '')),
    sold_num=shopee_prod.sold_num.apply(lambda x: x.replace(',', '')),
    stock_num=shopee_prod.in_stock.apply(lambda x: x.replace('還剩', '').replace('件', ''))
)
for col in ['spec']:
    shopee_prod[col] = shopee_prod[col].apply(lambda x: 'None' if len(x) == 0 else x)

for col in ['origin_price_floor','origin_price_ceil','sales_price_floor','sales_price_ceil',
            'review_score','review_num','sold_num','stock_num']:
    shopee_prod[col] = pd.to_numeric(shopee_prod[col], errors='coerce')
    
shopee_prod[['review_score','review_num','sold_num']] = shopee_prod[['review_score','review_num','sold_num']].fillna(0)
shopee_prod = shopee_prod[['title','description','spec','origin_price_floor','origin_price_ceil',
                           'sales_price_floor','sales_price_ceil','discount',
                           'review_score','review_num','sold_num','stock_num']]
shopee_prod.to_csv('Shopee/Preprocessed-Shopee-query=健身-productDetail.csv', index=False)
shopee_prod.info()
shopee_prod.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 998 entries, 0 to 997
Data columns (total 12 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   title               998 non-null    object 
 1   description         998 non-null    object 
 2   spec                998 non-null    object 
 3   origin_price_floor  998 non-null    float64
 4   origin_price_ceil   998 non-null    float64
 5   sales_price_floor   998 non-null    float64
 6   sales_price_ceil    998 non-null    float64
 7   discount            998 non-null    float64
 8   review_score        998 non-null    float64
 9   review_num          998 non-null    float64
 10  sold_num            998 non-null    float64
 11  stock_num           998 non-null    int64  
dtypes: float64(8), int64(1), object(3)
memory usage: 93.7+ KB


title  \
0  台灣公司貨+開箱影片 多功能俯臥撐板 俯臥撐支架 健身器材 胸肌訓練器 伏地挺身訓練 健身 ...   
1  拉力繩 功能環狀彈力帶 拉力帶 瑜珈繩 彈力繩 健身 訓練帶 重訓阻力繩 專業11套讓你帶著...   
2  【居家健身】現貨免運 健身組合 DDS健身椅+環保啞鈴組 坐姿划船 大腿延伸 臥推 肩推 划...   
3  【現貨 免運費！電子升級款 贈防滑墊】多功能俯臥撐板 健身器材 重量訓練器材 伏地挺身板 二...   
4  【未來實驗室】URBANFITNESS 城市健身組 36kg/60kg啞鈴組+健身椅 坐姿划...   

                                         description  \
0  網拍首選 上班時間皆有出貨 （例假日除外） 收到訂單將立即為您安排   🧾每筆訂單開立電子發...   
1  全館商品滿７９９超商免運，歡迎至賣場參觀選購  現在完成訂單給予五星評價後截圖透過聊聊傳給客...   
2  現貨免運!! DDS多德士健身椅+啞鈴組(20/30/40/50kg任選)   本檔加入啞鈴...   
3  因重量限制，超商取貨最多僅能下單 4件，如要下單 5(含)以上請改用宅配方式配送。   捕夢...   
4  【優惠訊息】       夏季優惠全館不限金額免運實施中    全館商品8折優惠中   【產...   

                                                spec  origin_price_floor  \
0                                       電子計數款 普通CP值款               782.0   
1                                               None               380.0   
2  現貨-DDS健身椅+20kg啞鈴組 現貨-DDS健身椅+30kg啞鈴組 現貨-DDS健身椅+...              3800.0   
3                                            電子款 普通款               732.0   
4              A－3KG共36KG含健身椅共3箱 B - 5KG共60KG含健身椅共5箱              4999.0   

   origin_price_ceil  sales_price_floor  sales_price_ceil  discount  \
0              950.0              399.0             519.0      0.51   
1              380.0              299.0             299.0      0.79   
2             5000.0             2458.0            3158.0      0.62   
3              882.0              399.0             499.0      0.55   
4             5623.0             3999.0            4499.0      0.80   

   review_score  review_num  sold_num  stock_num  
0           4.9      1375.0    2690.0    1997641  
1           4.9       536.0    1002.0        635  
2           4.9      1559.0    3100.0        371  
3           4.9       743.0    1426.0       2684  
4           4.8      2324.0    4185.0        258

In [ ]:
ec_486 = pd.read_csv('octoparse_export/486-searchResult-20210831T094900.csv')
for col in ec_486.columns:
    if ec_486[col].dtype == 'O':
        ec_486[col] = ec_486[col].fillna(' ')
        ec_486[col] = ec_486[col].apply(lambda x: x.strip())
    else:
        ec_486[col] = ec_486[col].fillna(0)
cond_list = [
    ec_486['sales_num'].str.contains('售完'),
    ec_486['sales_num'].str.contains('99+')
]
choice_list = ['0', '999']
ec_486['sales_num'] = np.select(condlist=cond_list, choicelist=choice_list, default=ec_486['sales_num'])
ec_486['sales_num'] = ec_486['sales_num'].apply(lambda x: 1000 - int(''.join(re.findall('[0-9]', x))) if ''.join(re.findall('[0-9]', x)) != '' else 0)
ec_486 = ec_486.drop(['url', 'current_time'], axis=1)

ec_486['keywords'] = ec_486[['title', 'label', 'description', 'spec', 'related_products']].agg(' '.join, axis=1)
ec_486 = add_wordCut_col(df=ec_486, method='ckipWs', col_list=['keywords'])
ec_486 = ec_486.drop(['title', 'label', 'description', 'spec', 'related_products','keywords'], axis=1)
ec_486.info()
ec_486.head()

# tf-idf
ec_486_tfidf = get_tfidf_col(df=ec_486, index_col='product_id', kw_col='keywords_ckipWs')
pick_col = [col for col in ec_486_tfidf.columns if not re.search('[0-9]+', col)]
ec_486_tfidf = ec_486_tfidf[pick_col]

# stack by keywrods
ec_486_ = ec_486.reset_index().rename(columns={'index': 'product_id'})
ec_486_ = pd.merge(ec_486_, mamilove_tfidf, on='product_id', how='left').drop_duplicates()
ec_486_ = ec_486_.drop('keywords_ckipWs', axis=1).join(ec_486_['keywords_ckipWs']
                                      .str
                                      .split(' ', expand=True)
                                      .stack()
                                      .reset_index(drop=True, level=1)
                                      .rename('keywords_ckipWs'))
ec_486_ = ec_486_[ec_486_['keywords_ckipWs'].notnull()].reset_index(drop=True)
ec_486_.head()


# 關鍵詞量化指標
ec_486_['tfidf_score'] = ec_486_.apply(lambda row: get_tfidf_score(row, df=ec_486_, kw_col='keywords_ckipWs'), axis=1)
pick_col = ['product_id'] + [col for col in ec_486_ if col not in ec_486_tfidf.columns]
keyword_metrics = ec_486_[pick_col]
keyword_metrics.to_csv('ec_486/ec_486-keyword_metrics.csv', index=False)
keyword_metrics

# no tf-idf
keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  }).sort_values('sales_num', ascending=False).head(100)

# with tf-idf
TFI_keyword_metrics = keyword_metrics.copy()
for col in ['sales_num']:
    TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']
TFI_keyword_metrics.to_csv('ec_486/ec_486-keyword_metrics_TFIDFweighted.csv', index=False)
TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  }).sort_values('sales_num', ascending=False).head(100)

In [27]:
mamilove = pd.read_csv('octoparse_export/mamilove-searchResult-20210830T214700.csv')
mamilove.columns = ['title', 'image', 'description', 'sales_num', 'sales_price', 'review_score']
mamilove['sales_num'] = mamilove['sales_num'].apply(lambda x: x.replace('已售出', '').replace('最新開團', '').strip())
mamilove['sales_num'] = pd.to_numeric(mamilove['sales_num'], errors='coerce')
mamilove = mamilove[(mamilove['sales_price'].notnull()) & (mamilove['review_score'].notnull()) & (mamilove['sales_num'].notnull())].reset_index(drop=True)
mamilove = mamilove.drop(['image'], axis=1)
for col in mamilove.columns:
    if mamilove[col].dtype == 'O':
        mamilove[col] = mamilove[col].apply(lambda x: remove_punctuation(remove_emoji(remove_link(x.strip()))))
        
mamilove['keywords'] = mamilove[['title', 'description']].agg(' '.join, axis=1)
mamilove = add_wordCut_col(df=mamilove, method='ckipWs', col_list=['keywords'])
mamilove = mamilove.drop(['title', 'description', 'keywords'], axis=1)
mamilove.info()
mamilove.head()

# tf-idf
mamilove_tfidf = get_tfidf_col(df=mamilove, index_col='product_id', kw_col='keywords_ckipWs')
pick_col = [col for col in mamilove_tfidf.columns if not re.search('[0-9]+', col)]
mamilove_tfidf = mamilove_tfidf[pick_col]

# stack by keywrods
mamilove = mamilove.reset_index().rename(columns={'index': 'product_id'})
mamilove = pd.merge(mamilove, mamilove_tfidf, on='product_id', how='left').drop_duplicates()
mamilove = mamilove.drop('keywords_ckipWs', axis=1).join(mamilove['keywords_ckipWs']
                                      .str
                                      .split(' ', expand=True)
                                      .stack()
                                      .reset_index(drop=True, level=1)
                                      .rename('keywords_ckipWs'))
mamilove = mamilove[mamilove['keywords_ckipWs'].notnull()].reset_index(drop=True)
mamilove.head()


# 關鍵詞量化指標
mamilove['tfidf_score'] = mamilove.apply(lambda row: get_tfidf_score(row, df=mamilove, kw_col='keywords_ckipWs'), axis=1)
pick_col = ['product_id'] + [col for col in mamilove if col not in mamilove_tfidf.columns]
keyword_metrics = mamilove[pick_col]
keyword_metrics.to_csv('mamilove/mamilove-keyword_metrics.csv', index=False)
keyword_metrics

# no tf-idf
keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  'sales_price': 'mean', 'review_score': 'mean'}).sort_values('sales_num', ascending=False).head(100)

# with tf-idf
TFI_keyword_metrics = keyword_metrics.copy()
for col in ['sales_num','sales_price','review_score']:
    TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']
    
TFI_keyword_metrics.to_csv('mamilove/mamilove-keyword_metrics_TFIDFweighted.csv', index=False)
TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  'sales_price': 'mean', 'review_score': 'mean'}).sort_values('sales_num', ascending=False).head(100)


product_id  sales_num  sales_price  review_score keywords_ckipWs  \
0               0    10899.0         84.0           4.9              新手   
1               0    10899.0         84.0           4.9              媽咪   
2               0    10899.0         84.0           4.9              救星   
3               0    10899.0         84.0           4.9              營養   
4               0    10899.0         84.0           4.9              常溫   
...           ...        ...          ...           ...             ...   
15890         765     1444.0        239.0           4.8               ✔   
15891         765     1444.0        239.0           4.8              療癒   
15892         765     1444.0        239.0           4.8              亮片   
15893         765     1444.0        239.0           4.8              安撫   
15894         765     1444.0        239.0           4.8              寶寶   

       tfidf_score  
0         0.238169  
1         0.155927  
2         0.255904  
3         0.458785  
4         0.286222  
...            ...  
15890     0.000000  
15891     0.000000  
15892     0.000000  
15893     0.000000  
15894     0.000000  

[15895 rows x 6 columns]

product_id  sales_num  sales_price  review_score
keywords_ckipWs                                                  
日本                      200  1085197.0   327.814815      4.873663
推薦                       34  1039061.0   219.540541      4.837838
折                       117   969757.0   473.512821      4.782906
便宜                        8   798973.0   262.900000      4.910000
圖卡                        8   790315.0   117.545455      4.827273
獨家                       31   701312.0   576.064516      4.880645
熱銷                       50   650874.0   342.215686      4.868627
精選                       26   634819.0   196.035714      4.860714
繪本                       12   632729.0   208.625000      4.812500
寶寶                       67   632042.0   462.400000      4.866667
媽咪                       58   628195.0   367.406780      4.859322
視覺                        7   625668.0   169.375000      4.662500
必備                       81   546161.0   258.228916      4.825301
歲                        44   540619.0   325.660000      4.790000
❤                        54   492627.0   363.550000      4.816667
品牌                       50   480404.0   172.500000      4.866667
兒童                       63   467718.0   322.746269      4.864179
集合                       33   425408.0   212.470588      4.852941
☀                         5   422292.0   192.000000      4.877778
童書                        5   417420.0    72.750000      4.875000
愛                        37   417256.0   430.750000      4.870000
病毒                       10   402644.0   496.714286      4.828571
親子                       23   394875.0   158.655172      4.906897
件                        48   388663.0   280.940000      4.806000
平臺                       19   384097.0   502.894737      4.815789
小時報                       2   378492.0   127.000000      4.900000
超過                        6   347628.0   231.500000      4.716667
細菌                       21   339481.0   249.619048      4.809524
次                        25   335796.0   217.520000      4.768000
祕密                        6   321368.0   169.100000      4.850000
任選                       30   319403.0   239.433333      4.823333
年                        25   317175.0   204.080000      4.876000
孩子                       77   313096.0   249.455556      4.852222
新生兒                      16   306069.0   335.937500      4.881250
做                        11   304728.0   165.363636      4.854545
奶瓶                       12   296707.0   218.769231      4.846154
好物                       26   296380.0    98.769231      4.876923
奶嘴                       10   288672.0   140.333333      4.841667
全                        44   281864.0   396.956522      4.860870
位                         6   281068.0   151.000000      4.866667
育兒                       18   270039.0   440.611111      4.816667
安心                       50   265165.0   412.058824      4.813725
免運                       11   264786.0   354.181818      4.863636
動手                        4   264464.0   162.500000      4.850000
好評                       14   264381.0   524.928571      4.857143
發展                       10   263464.0   192.909091      4.809091
玩                        38   257470.0   305.102564      4.817949
防                        54   257467.0   284.173333      4.761333
黑白                        3   254122.0    96.000000      4.900000
買                        28   252135.0   849.900000      4.896667
圍兜                       14   251815.0   290.066667      4.826667
五星                        2   250636.0    95.000000      4.900000
臺灣製                       9   245407.0   143.000000      4.866667
媽媽                       26   238561.0   419.592593      4.885185
童裝                       28   237974.0   295.916667      4.908333
大公開                       6   237877.0   170.666667      4.883333
舖                        27   232073.0   154.758621      4.924138
♥                        12   228506.0   498.400000      4.826667
人氣                       33   226668.0   211.200000      

product_id     sales_num  sales_price  review_score
keywords_ckipWs                                                     
推薦                       34  41084.057059     5.570111      0.122828
寶寶                       67  27492.005081     8.049898      0.172911
媽咪                       58  22413.826290    14.662136      0.127309
品牌                       50  19980.578557    11.137987      0.183600
熱銷                       50  17279.864373    13.418702      0.128955
日本                      200  16098.874409     9.808211      0.096095
必備                       81  11602.874939     3.027754      0.068322
營養                       10  10000.590683     6.422987      0.374674
幼童                        7   8504.221127     1.089939      0.296706
安心                       50   7075.625969    25.326424      0.109796
好物                       26   6433.952319     0.798124      0.066740
選擇                       11   5510.855387     2.542976      0.198926
大公開                       6   5089.832354     1.534180      0.156614
系列                       19   5040.539805     0.221528      0.053167
開學                       19   4910.572450     2.191128      0.138903
經典                       12   4879.693714     0.014522      0.071157
材質                       35   3274.440839     1.374879      0.043996
常溫                        2   3119.528476    12.021304      0.701243
熬煮                        2   3119.528476    12.021304      0.701243
新鮮                        4   2876.012945     5.541451      0.323251
加熱                        4   2876.012945     5.541451      0.323251
寶寶粥                       4   2876.012945     5.541451      0.323251
救星                        5   2789.098490     4.299188      0.250786
省時                        5   2789.098490     4.299188      0.250786
食材                        5   2789.098490     4.299188      0.250786
文具                       11   2721.873752     2.655141      0.125171
歐美                        9   2689.008422    19.223512      0.196136
新手                        8   2595.809338     2.500780      0.145879
透氣                       59   2508.145802     2.123884      0.058647
角落                       13   2243.499005     6.720432      0.152121
添加                       21   2169.717684     0.760104      0.044339
新款                       10   1987.114991     2.670375      0.085452
通通                       32   1969.111034     0.972830      0.031131
登場                       19   1805.397284     6.219136      0.111163
獨家                       31   1598.815948     0.597662      0.046764
睡袋                        8   1468.093465   329.995376      1.312262
專區                        3   1454.669135    11.482856      0.501070
柔軟                       54   1333.512933     1.072401      0.021538
正版                       11   1232.060785     6.945285      0.098340
集合                       33   1170.487046     1.123958      0.042528
育兒                       18   1063.406335     1.324864      0.132486
上學                       21    895.065998     5.301618      0.083743
時尚                       23    805.122316    13.278170      0.166614
韓國                       51    640.901723    12.114293      0.125100
可愛                       35    590.219911     2.505029      0.041098
學習                       34    560.098160     1.108705      0.057019
授權                       13    533.228281    18.459073      0.150532
重複                       14    530.811200     5.042382      0.123143
百搭                       20    508.715846    17.906726      0.169851
過濾                       10    452.510048     3.947948      0.093999
兒童                       63    420.095246     1.955206      0.031183
人氣                       33    416.370127    10.080040      0.122363
cm                       40    400.758962     8.082105      0.071205
日本製                      27    399.789178     2.151941      0.040556
卡通                       21    385.494337     3.628460      0.040504
品質                       12    380.396017     4.146185      0.105300
生活             

In [27]:
freemart = pd.read_csv('octoparse_export/freemart-searchResult-20210830T214700.csv')
freemart.columns = ['title', 'image', 'url', 'info', 'button', 'sales_num', 'description']
freemart = freemart.drop(['image', 'url', 'button', 'info'], axis=1)
freemart['sales_num'] = freemart['sales_num'].apply(lambda x: int(x.replace('已搶購', '').strip()))
for col in freemart.columns:
    if freemart[col].dtype == 'O':
        freemart[col] = freemart[col].apply(lambda x: remove_punctuation(remove_emoji(remove_link(x.strip()))))
        
freemart['keywords'] = freemart[['title', 'description']].agg(' '.join, axis=1)
freemart = add_wordCut_col(df=freemart, method='ckipWs', col_list=['keywords'])
freemart = freemart.drop(['title', 'description', 'keywords'], axis=1)

# tf-idf
freemart_tfidf = get_tfidf_col(df=freemart, index_col='product_id', kw_col='keywords_ckipWs')
pick_col = [col for col in freemart_tfidf.columns if not re.search('[0-9]+', col)]
freemart_tfidf = freemart_tfidf[pick_col]

# stack by keywrods
freemart = freemart.reset_index().rename(columns={'index': 'product_id'})
freemart = pd.merge(freemart, freemart_tfidf, on='product_id', how='left').drop_duplicates()
freemart = freemart.drop('keywords_ckipWs', axis=1).join(freemart['keywords_ckipWs']
                                      .str
                                      .split(' ', expand=True)
                                      .stack()
                                      .reset_index(drop=True, level=1)
                                      .rename('keywords_ckipWs'))
freemart = freemart[freemart['keywords_ckipWs'].notnull()].reset_index(drop=True)
freemart.info()
freemart.head()

# 關鍵詞量化指標
freemart['tfidf_score'] = freemart.apply(lambda row: get_tfidf_score(row, df=freemart, kw_col='keywords_ckipWs'), axis=1)
pick_col = ['product_id'] + [col for col in freemart if col not in freemart_tfidf.columns]
keyword_metrics = freemart[pick_col]
keyword_metrics.to_csv('freemart/freemart-keyword_metrics.csv', index=False)
keyword_metrics

# no tf-idf
keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  }).sort_values('sales_num', ascending=False).head(100)

# with tf-idf
TFI_keyword_metrics = keyword_metrics.copy()
for col in ['sales_num']:
    TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']
    
TFI_keyword_metrics.to_csv('freemart/freemart-keyword_metrics_TFIDFweighted.csv', index=False)
TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 'sales_num': 'sum', 
                                                  }).sort_values('sales_num', ascending=False).head(100)



product_id      sales_num
keywords_ckipWs                           
美味                       37  208266.172747
團購                       12   60641.728393
雞絲麵                       2   55373.209318
吉好                        1   54734.431630
系列                       29   48310.080060
美食                        9   46704.288494
熱銷                       10   37336.202653
獨特                        7   29205.675434
肉肉                        2   23803.163655
醬汁                        4   22821.631785
上桌                        4   21684.798772
技術                        7   20973.448758
嚴選                       21   19053.797487
防疫                        9   18022.510123
酥脆                       15   17572.771174
牛肉                        3   16163.211923
加碼                        1   13683.607907
實惠                        1   13683.607907
輕鬆                        9   13642.190608
好評                        3   13040.001745
料理                        6   12853.979996
優良                        2   12649.089255
金牌獎                       2   12649.089255
高纖                        2   12649.089255
經濟                        3   12579.733925
低卡                        3   11915.086591
國家                        4   11345.749893
合格                        5   10880.567939
榮獲                        7   10146.565274
檢驗                       26   10005.270548
臺灣                       32    9975.746286
商品                        9    9577.228576
搭配                        6    9374.701301
汙染                        6    6394.363922
排隊                        3    6027.703102
濃鬱                       17    6023.472313
均勻                        2    5950.790914
油花                        2    5950.790914
向來                        2    5950.790914
備好                        2    5950.790914
分佈                        2    5950.790914
全球                        2    5950.790914
深受                        2    5950.790914
飼養                        3    5905.320065
市場                        3    5605.477801
消費者                       3    5605.477801
推薦                       19    5471.254428
豬肉                        4    5337.632142
通通                        4    5337.632142
標準                        6    4933.754783
錯過                        7    3247.276381
香脆                        6    3047.481841
金黃                        4    2869.841159
分鐘                       14    1361.210176
品味                        2     584.088333
冠軍                        4     440.807344
研發                        3     163.136429
紅棗                        1       0.000000
紅燒                        2       0.000000
紅肉                        1       0.000000
紅寶石                       1       0.000000
糖精                        1       0.000000
花腱肉                       1       0.000000
紅到                        1       0.000000
花蓮                        3       0.000000
花生香                       1       0.000000
糖心                        1       0.000000
精選                        5       0.000000
精製                        3       0.000000
精華液                       1       0.000000
花蜜                        1       0.000000
精華                        1       0.000000
精緻                        1       0.000000
精梳棉                       1       0.000000
紅茶                        1       0.000000
納豆菌                       1       0.000000
花生菓                       1       0.000000
紅豆                        1       0.000000
花                         1       0.000000
花生                        3       0.000000
終身                        1       0.000000
細菌                        1       0.000000
細膩                        1       0.000000
細緻                        7       0.000000
細綿                        1       0.000000
細滑                        1       0.000000
細心                        1       0.000000
細                         2       0.000000
紮實                        5       0.000000
紫光燈                       1       0.000000
紫光                        1       0.000000
素食界               

In [57]:
# buy123 = pd.read_csv('octoparse_export/buy123-searchResult-20210830T214700.csv')
# buy123.columns = ['keywords', 'label1', 'image', 'origin_price', 'label2', 'sales_price', 'review', 'sales_num', 'image2']
# buy123[['review_score', 'review_num']] = buy123['review'].str.split('(', 1, expand=True)
# buy123 = buy123.drop(['image','image2','label1', 'label2','review'], axis=1)

# for col in ['origin_price', 'sales_price', 'sales_num', 'review_score', 'review_num']:
#     buy123[col] = buy123[col].apply(lambda x: float('.'.join(re.findall('[0-9]+', x))))
# buy123['keywords'] = buy123['keywords'].apply(lambda x: remove_punctuation(remove_emoji(remove_link(x.strip()))))
# buy123 = add_wordCut_col(df=buy123, method='ckipWs', col_list=['keywords'])
# buy123 = buy123.drop(['keywords'], axis=1)

# # tf-idf
# buy123_tfidf = get_tfidf_col(df=buy123, index_col='product_id', kw_col='keywords_ckipWs')
# pick_col = [col for col in buy123_tfidf.columns if not re.search('[0-9]+', col)]
# buy123_tfidf = buy123_tfidf[pick_col]

# # stack by keywrods
# buy123 = buy123.reset_index().rename(columns={'index': 'product_id'})
# buy123 = pd.merge(buy123, buy123_tfidf, on='product_id', how='left').drop_duplicates()
# buy123 = buy123.drop('keywords_ckipWs', axis=1).join(buy123['keywords_ckipWs']
#                                       .str
#                                       .split(' ', expand=True)
#                                       .stack()
#                                       .reset_index(drop=True, level=1)
#                                       .rename('keywords_ckipWs'))
# buy123 = buy123[buy123['keywords_ckipWs'].notnull()].reset_index(drop=True)
# buy123.info()
# buy123.head()

# # 關鍵詞量化指標
# buy123['tfidf_score'] = buy123.apply(lambda row: get_tfidf_score(row, df=buy123, kw_col='keywords_ckipWs'), axis=1)
# pick_col = ['product_id'] + [col for col in buy123 if col not in buy123_tfidf.columns]
# keyword_metrics = buy123[pick_col]
# keyword_metrics.to_csv('buy123/buy123-keyword_metrics.csv', index=False)
# keyword_metrics

# # no tf-idf
# keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
#                                                   'origin_price': 'mean', 'sales_price': 'mean', 
#                                                   'sales_num': 'sum', 'review_score': 'mean', 'review_num': 'sum'
#                                                   }).sort_values('sales_num', ascending=False).head(100)

# # with tf-idf
# TFI_keyword_metrics = keyword_metrics.copy()
# for col in ['sales_num']:
#     TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']
    
# TFI_keyword_metrics.to_csv('buy123/buy123-keyword_metrics_TFIDFweighted.csv', index=False)
# TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
#                                                   'origin_price': 'mean', 'sales_price': 'mean', 
#                                                   'sales_num': 'sum', 'review_score': 'mean', 'review_num': 'sum'
#                                                   }).sort_values('sales_num', ascending=False).head(100)

# 重跑

product_id  origin_price  sales_price   sales_num  \
keywords_ckipWs                                                      
衛生紙                     149     49.031333    40.403333  73725663.0   
生活                       20    206.566667   112.023810  40463909.0   
市集                       13    122.023077    71.023077  40450311.0   
低價                        1      7.600000     5.700000  35628100.0   
口罩                      129     90.961240    53.006202  24043807.0   
抽取                       52     37.617308    26.257692  18434413.0   
抽取式                      65     21.643077    14.858462  17721906.0   
超                       316    553.198113   356.344654  17665609.0   
防滑                      154    292.761688   160.637662  17615654.0   
衣架                       59    550.376271   367.900000  16353375.0   
純水                       25    156.212000   123.268000  15953851.0   
溶水                       17     10.047059     7.876471  14968867.0   
不鏽鋼                     514    804.623735   554.141634  13314975.0   
兩用                      178   1173.139888   842.973034  12135713.0   
濕                        43    310.488372   181.844186  12098821.0   
乾                        64    396.101562   234.510937  12031402.0   
柔濕巾                      14     43.550000    33.142857  11850022.0   
拋棄式                      18     83.650000    37.583333  10779637.0   
日本                      292    819.412329   599.858904  10116941.0   
層                       238   1091.260581   793.134440   9573645.0   
奈森克林                      8     22.537500    11.612500   8902633.0   
活性碳                       9    487.155556   339.433333   8856788.0   
洗衣膠球                     13     19.730769    12.761538   8403584.0   
頂級                      183   1229.470492   878.633880   8252381.0   
臺灣製                     145   1050.819310   754.591724   7996745.0   
濕巾                       22    170.527273   138.140909   7810753.0   
紙尿褲                      34    315.955882   260.394118   7743370.0   
純柔                       12     11.158333     8.641667   7718698.0   
嬰兒                       48    618.543750   486.506250   7584442.0   
水滴                        5     40.180000    27.300000   6834905.0   
系列                      258    847.844574   641.928295   6655052.0   
溶                         4     11.225000     7.575000   6577016.0   
手工                       53    661.077358   478.901887   6444841.0   
噴                         2    288.750000   128.900000   6249498.0   
柔                        22    202.036364   129.840909   6012893.0   
水餃                       14     77.742857    41.642857   5906585.0   
成人                       37    215.067568   154.975676   5503990.0   
抽                        51   1075.367308   820.580769   5484551.0   
牙線棒                       4      0.775000     0.525000   5281095.0   
細滑                        4      0.775000     0.525000   5281095.0   
熊                        23    422.600000   279.486957   5244068.0   
益生菌                      21    153.395238   124.690476   5166085.0   
補充包                      19    242.478947   173.789474   5161486.0   
飽滿                       10    233.570000   129.270000   5074030.0   
韓國                      103    536.803883   356.226214   4916413.0   
防護墊                       2    201.050000   121.000000   4896132.0   
強效                       48    374.239583   242.466667   4893897.0   
寶適                       18      8.366667     6.905556   4796852.0   
酒精                       66    369.781818   225.030303   4621592.0   
尿布                       26     23.142308    15.007692   4462833.0   
汙                        44    256.597727   162.075000   4307981.0   
紙巾                       42    137.535714    76.883333   4173261.0   
幫                        15      9.083333     7.538889   4038965.0   
五月花                      24     51.650000    42.145833   3921646.0   
熱銷                      181    532.377901   343.239779   3785547.0   
濕紙巾                      16

product_id  origin_price  sales_price      sales_num  \
keywords_ckipWs                                                         
寶適                       18      8.366667     6.905556  561265.574578   
日本                      292    819.412329   599.858904  448470.442330   
韓國                      103    536.803883   356.226214  213898.473017   
寶寶                       38    587.397436   400.882051  153793.600922   
滿意                        9     11.211111     9.555556   91185.572227   
乾爽                       16    168.012500   120.556250   61663.713491   
紙尿褲                      34    315.955882   260.394118   56926.151839   
立體                      104    555.334615   374.607692   44009.282328   
環保                      123    332.309756   201.069106   32193.283013   
氣炸鍋                      38   1892.952632  1479.100000   27223.581239   
兒童                      284    735.771479   514.306690   24708.794977   
廚房                      161    636.796273   407.391304   21851.425152   
熱銷                      181    532.377901   343.239779   16051.233285   
收納                      476   1348.661765   974.127311   12544.092655   
透氣                      295    731.177966   471.375593   12042.541086   
吸水                       84    279.534524   130.602381   12021.369289   
多功能                     367   1063.903270   741.945504   11650.657512   
居家                       66    998.330303   704.481818    6466.556229   
地墊                      109    482.175229   276.344037    5584.736644   
水洗                       72    980.612500   716.300000    4785.405163   
防滑                      154    292.761688   160.637662    3869.336514   
不銹鋼                      83    614.628916   404.506024    3417.657824   
床包                       79    973.683544   711.098734    3081.134871   
系列                      258    847.844574   641.928295    2718.591126   
加大                      147    692.229252   451.982993    2573.496654   
防水                      302    602.481188   381.497030    2531.945339   
純棉                       79    529.820253   338.284810    2500.259403   
置物架                     195    859.600000   559.512245    2221.891488   
兩用                      178   1173.139888   842.973034    2032.191076   
空氣                      104   3410.923077  2763.464423    1817.253447   
睡袋                       17   1318.352941  1023.529412    1716.372462   
仿真                       16    457.037500   269.281250    1646.924967   
加厚                      185    700.543243   451.959459    1580.201809   
頂級                      183   1229.470492   878.633880    1254.749605   
日式                      201    960.724876   654.378607    1187.113796   
舒適                      132    676.848485   440.774242    1053.229691   
收納架                     151    764.186093   501.011258    1041.280203   
雙層                      145    613.982069   380.824828    1019.451392   
不鏽鋼                     514    804.623735   554.141634     997.022422   
馬卡龍                      35    949.297143   668.988571     955.495486   
牙刷                       57    698.057895   495.954386     645.140766   
衛生紙                     149     49.031333    40.403333     595.873326   
便攜                       64    679.273438   424.050000     568.517332   
臺灣製                     145   1050.819310   754.591724     564.941372   
簡約                      119    899.847899   611.359664     534.036663   
自動                      168   1153.385714   826.245238     490.322401   
玻璃                      154    619.784416   399.996104     439.155858   
休閒                       58    580.722414   339.853448     415.403179   
美白                        6     32.566667    13.116667     405.602578   
吸濕                       38    492.168421   306.294737     398.430250   
排汗                       41    515.039024   317.409756     394.163573   
耐重                       41    902.853659   593.346341     385.146660   
珪藻土                      33    342.754545   178.645455     370.366470   
巧福

In [125]:
# ihergo = pd.read_csv('octoparse_export/ihergo-searchResult-20210830T214700.csv')
# ihergo.columns = ['keywords', 'url', 'image', 'discount_rate1', 'label', 'origin_price', 'sales_price0', 'sales_price', 
#                   'discount_rate2', 'label2', 'sales_num', 'review_score']
# # ihergo = ihergo[(ihergo['title'].notnull()) & (ihergo['review_score'].notnull())].reset_index(drop=True)
# ihergo = ihergo.drop(['url','image','label','sales_price0','label2'], axis=1)

# for col in ['discount_rate1','origin_price','sales_price','discount_rate2','sales_num','review_score']:
#     ihergo[col] = ihergo[col].apply(lambda x: '.'.join(re.findall('[0-9]+', str(x).replace('折','')
#                                                                         .replace('原價','')
#                                                                         .replace('$','')
#                                                                         .replace('起','')
#                                                                         .replace('再',''))))
#     ihergo[col] = pd.to_numeric(ihergo[col], errors='coerce')
#     if col == 'discount_rate2':
#         ihergo[col] = ihergo[col].fillna(10.0)
#     elif col == 'sales_num':
#         ihergo[col] = ihergo[col].fillna(0.0)
#     elif col == 'review_score':
#         ihergo[col] = ihergo[col].fillna(np.mean(ihergo[col]))
#     else:
#         pass

# ihergo['discount_rate1'] = ihergo['discount_rate1'] / 10
# ihergo['discount_rate2'] = ihergo['discount_rate2'].apply(lambda x: float(str(int(x))[:1] + '.' + str(int(x))[1:]))
# ihergo['discount_rate2'] = ihergo['discount_rate2'].apply(lambda x: x / 10 if x != 1 else x)
# ihergo['discount_rate'] = ihergo['discount_rate1'] * ihergo['discount_rate2'] 

# ihergo = add_wordCut_col(df=ihergo, method='ckipWs', col_list=['keywords'])
# ihergo = ihergo.drop(['keywords','discount_rate2','discount_rate1'], axis=1)

# # tf-idf
# ihergo_tfidf = get_tfidf_col(df=ihergo, index_col='product_id', kw_col='keywords_ckipWs')
# pick_col = [col for col in ihergo_tfidf.columns if not re.search('[0-9]+', col)]
# ihergo_tfidf = ihergo_tfidf[pick_col]

# # stack by keywrods
# ihergo = ihergo.reset_index().rename(columns={'index': 'product_id'})
# ihergo = pd.merge(ihergo, ihergo_tfidf, on='product_id', how='left').drop_duplicates()
# ihergo = ihergo.drop('keywords_ckipWs', axis=1).join(ihergo['keywords_ckipWs']
#                                       .str
#                                       .split(' ', expand=True)
#                                       .stack()
#                                       .reset_index(drop=True, level=1)
#                                       .rename('keywords_ckipWs'))
# ihergo = ihergo[ihergo['keywords_ckipWs'].notnull()].reset_index(drop=True)
# ihergo.info()
# ihergo.head()

# # 關鍵詞量化指標
# ihergo['tfidf_score'] = ihergo.apply(lambda row: get_tfidf_score(row, df=ihergo, kw_col='keywords_ckipWs'), axis=1)
# pick_col = ['product_id'] + [col for col in ihergo if col not in ihergo_tfidf.columns]
# keyword_metrics = ihergo[pick_col]
# keyword_metrics.to_csv('ihergo/ihergo-keyword_metrics.csv', index=False)
# keyword_metrics

# # no tf-idf
# keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
#                                                   'origin_price': 'mean', 'sales_price': 'mean', 'discount_rate': 'mean',
#                                                   'sales_num': 'sum', 'review_score': 'mean'
#                                                   }).sort_values('sales_num', ascending=False).head(100)

# # with tf-idf
# TFI_keyword_metrics = keyword_metrics.copy()
# for col in ['origin_price','sales_price','discount_rate','sales_num','review_score']:
#     TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']

# TFI_keyword_metrics.to_csv('ihergo/ihergo-keyword_metrics_TFIDFweighted.csv', index=False)
# TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
#                                                   'origin_price': 'mean', 'sales_price': 'mean', 'discount_rate': 'mean',
#                                                   'sales_num': 'sum', 'review_score': 'mean'
#                                                   }).sort_values('sales_num', ascending=False).head(100)




product_id  origin_price  sales_price  discount_rate  \
keywords_ckipWs                                                         
免                      1098    264.785168   140.621474       0.566091   
運                      1097    264.311668   140.389790       0.566185   
免運                      556    323.937702   160.684381       0.549863   
任選                      264    250.039394   110.534091       0.527400   
口味                      109    277.914414   102.846847       0.535768   
雞腿排                      34    207.537143    90.525714       0.442777   
蝦餅                       16    220.425000   117.275000       0.540994   
月亮                       12    237.233333   120.350000       0.504908   
卜蜂                       33    198.063636    84.818182       0.404624   
饗福                        1    125.000000    69.300000       0.558000   
系列                       60    259.090000   123.831667       0.504737   
去骨                       17    170.605882    96.482353       0.505312   
醃漬                        4    130.000000    41.550000       0.329025   
鹽酥雞                      28    221.910345   149.527586       0.669534   
鹹酥雞                      23    237.539130   160.360870       0.682443   
農莊                       23    332.334783   235.126087       0.766087   
綠野                       23    332.334783   235.126087       0.766087   
原味                       65    296.508955   184.131343       0.614364   
臺灣                       68    308.329412   155.363235       0.597910   
黑                        20    280.950000   116.065000       0.509540   
包                       109    299.592908   201.214184       0.680922   
食堂                        9     97.277778    44.766667       0.507933   
泰凱                        9     97.277778    44.766667       0.507933   
胡椒                       16    209.937500    58.231250       0.470263   
大成                       11    146.727273    65.181818       0.504455   
炙燒                        1    120.000000    39.000000       0.330000   
g                        49    381.296078   213.058824       0.577482   
紅燒                       32    288.803125   155.506250       0.583484   
杏鮑菇                       5    327.800000   139.160000       0.421120   
素食                       44    232.340909   120.263636       0.534077   
麻油                       15    286.250000   122.856250       0.510731   
水餃                       51    140.196667    78.658333       0.567958   
入                        60    562.709524   344.409524       0.604881   
猴頭                        1    250.000000    71.400000       0.285200   
番茄                        8    165.500000    96.312500       0.557412   
牛肉湯                      16    246.062500   133.143750       0.547194   
蠔油                        3    212.333333   132.133333       0.649833   
享點子                       1    199.000000   120.600000       0.607200   
養生                       27    213.777778   118.274074       0.547052   
雞湯                       16    355.833333   203.522222       0.538289   
獨享包                       9     85.555556    56.211111       0.648244   
艾其肯                       1     95.000000    68.400000       0.720000   
ichicken                  1     95.000000    68.400000       0.720000   
麵                        49    174.524590    78.777049       0.558215   
骨                        27    256.011111   147.877778       0.554541   
酥脆                       26    167.784615    81.073077       0.539723   
咔滋                        2    160.000000    55.100000       0.339500   
超人氣                      15    132.633333    59.886667       0.518313   
紅龍                       19    344.115789   170.636842       0.559553   
Lioncook                  3    119.333333    61.966667       0.584033   
KKLife                    7    216.185714    97.871429       0.552914   
雞腿                       16    636.105263   362.700000       0.531116   
獅                         2     84.000000    60.850000       0.708650   
總舖

product_id  origin_price  sales_price  discount_rate  \
keywords_ckipWs                                                         
口味                      109      4.550604     1.384216       0.007258   
任選                      264     10.832394     4.598991       0.019384   
免運                      556      9.265896     4.238723       0.019136   
迷你                       15     25.982357     2.834439       0.002887   
綠野                       23     15.726337     1.715600       0.001747   
農莊                       23     15.726337     1.715600       0.001747   
天婦羅                       6     26.627870    14.173018       0.149215   
食品                       48      0.163680     0.089342       0.003721   
美味                       64      5.922315     3.752510       0.008464   
鹹酥雞                      23     13.167568    10.520238       0.044502   
手工                       69      1.136929     0.581823       0.006259   
包裝                       26      4.470751     1.040606       0.003607   
基隆                        3      7.050967     3.845982       0.034870   
超人氣                      15      2.618671     1.642621       0.016664   
饅頭                       22      0.553840     0.318757       0.011519   
下單                      211      0.636654     0.399776       0.004206   
福袋                      212      0.632675     0.397277       0.004180   
老爸                       34      3.729399     2.376020       0.006271   
廚房                       35      3.607550     2.298389       0.006066   
物產                      258      2.371523     0.973826       0.004706   
上野                      258      2.371523     0.973826       0.004706   
鹽酥雞                      28      5.840567     4.826239       0.022157   
麻油                       15      3.447455     1.254128       0.006709   
日式                       42      0.500013     0.235721       0.005572   
紅龍                       19      5.075869     3.523712       0.013581   
好吃                       12      0.720945     0.366987       0.011140   
鮮奶                        5      1.028493     0.591938       0.021391   
素食                       44      0.423437     0.174668       0.001461   
臺灣                       68      8.829797     4.300687       0.009628   
麻辣                       54      7.284298     1.219391       0.000830   
茶鵝                        2    117.533292    81.919821       0.204785   
鹹水                        4     54.660984    38.098295       0.095239   
煙燻                       14     13.094601     9.126838       0.022815   
辣味                       11      4.135911     3.470029       0.011539   
系列                       60      4.650479     2.871515       0.001914   
臺客                        2      0.000000     0.000000       0.000000   
臭豆腐                       9      0.000000     0.000000       0.000000   
臺味                        1      0.000000     0.000000       0.000000   
自由                        6      0.000000     0.000000       0.000000   
臺                         3      0.000000     0.000000       0.000000   
臺中                        1      0.000000     0.000000       0.000000   
臺南                        6      0.000000     0.000000       0.000000   
臺北                       29      0.000000     0.000000       0.000000   
臺全                        7      0.000000     0.000000       0.000000   
-                         4      0.000000     0.000000       0.000000   
自然                        8      0.000000     0.000000       0.000000   
自信                        1      0.000000     0.000000       0.000000   
脆皮                       15      0.000000     0.000000       0.000000   
脆脆                        1      0.000000     0.000000       0.000000   
脆腸                        1      0.000000     0.000000       0.000000   
脆薯                        5      0.000000     0.000000       0.000000   
脖子                        1      0.000000     0.000000       0.000000   
腐皮                        2      0.000000     0.000000       0.000000   
腐皮

In [136]:
ec_17life = pd.read_csv('octoparse_export/17life-searchResult-20210830T214700.csv')
ec_17life.columns = ['title', 'url', 'image', 'sales_num', 'label', 'description', 'info', 
                     'origin_price', 'discount_rate', 'info2', 'sales_price']
ec_17life = ec_17life.drop(['url','image','label','info','info2'], axis=1)

for col in ec_17life.columns:
    if ec_17life[col].dtype == 'O':
        ec_17life[col] = ec_17life[col].fillna(' ')
        if col in ['sales_num','origin_price','discount_rate','sales_price']:
            ec_17life[col] = ec_17life[col].apply(lambda x: x.replace('人已購買','')
                                                                  .replace('特選','')
                                                                  .replace('$','')
                                                                  .replace('折','').strip())
            ec_17life[col] = pd.to_numeric(ec_17life[col], errors='coerce')
            ec_17life[col] = ec_17life[col].fillna(10.0)
        else:
            ec_17life[col] = ec_17life[col].apply(lambda x: remove_punctuation(remove_emoji(remove_link(x.strip()))))
ec_17life['discount_rate'] = ec_17life['discount_rate'] / 10

ec_17life['keywords'] = ec_17life[['title', 'description']].agg(' '.join, axis=1)
ec_17life = add_wordCut_col(df=ec_17life, method='ckipWs', col_list=['keywords'])
ec_17life = ec_17life.drop(['title','description','keywords'], axis=1)

# tf-idf
ec_17life_tfidf = get_tfidf_col(df=ec_17life, index_col='product_id', kw_col='keywords_ckipWs')
pick_col = [col for col in ec_17life_tfidf.columns if not re.search('[0-9]+', col)]
ec_17life_tfidf = ec_17life_tfidf[pick_col]

# stack by keywrods
ec_17life = ec_17life.reset_index().rename(columns={'index': 'product_id'})
ec_17life = pd.merge(ec_17life, ec_17life_tfidf, on='product_id', how='left').drop_duplicates()
ec_17life = ec_17life.drop('keywords_ckipWs', axis=1).join(ec_17life['keywords_ckipWs']
                                      .str
                                      .split(' ', expand=True)
                                      .stack()
                                      .reset_index(drop=True, level=1)
                                      .rename('keywords_ckipWs'))
ec_17life = ec_17life[ec_17life['keywords_ckipWs'].notnull()].reset_index(drop=True)
ec_17life.info()
ec_17life.head()

# 關鍵詞量化指標
ec_17life['tfidf_score'] = ec_17life.apply(lambda row: get_tfidf_score(row, df=ec_17life, kw_col='keywords_ckipWs'), axis=1)
pick_col = ['product_id'] + [col for col in ec_17life if col not in ec_17life_tfidf.columns]
keyword_metrics = ec_17life[pick_col]
keyword_metrics.to_csv('ec_17life/ec_17life-keyword_metrics.csv', index=False)
keyword_metrics


# no tf-idf
keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
                                                  'origin_price': 'mean', 'sales_price': 'mean', 'discount_rate': 'mean',
                                                  'sales_num': 'sum'
                                                  }).sort_values('sales_num', ascending=False).head(100)

# with tf-idf
TFI_keyword_metrics = keyword_metrics.copy()
for col in ['origin_price','sales_price','discount_rate','sales_num']:
    TFI_keyword_metrics[col] = TFI_keyword_metrics[col] * TFI_keyword_metrics['tfidf_score']

TFI_keyword_metrics.to_csv('ec_17life/ec_17life-keyword_metrics_TFIDFweighted.csv', index=False)
TFI_keyword_metrics.groupby(['keywords_ckipWs']).agg({'product_id': 'nunique', 
                                                  'origin_price': 'mean', 'sales_price': 'mean', 'discount_rate': 'mean',
                                                  'sales_num': 'sum'
                                                  }).sort_values('sales_num', ascending=False).head(100)



Tokenization: 100%|█████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 110.81it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  1.09it/s]

Tokenization: 100%|█████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 665.02it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.76it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1994.44it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 11.94it/s]

Tokenization: 100%|█████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 997.46it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 12.87it/s]

Tokenization: 100%|█████████████

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 19.52it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.49it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.60it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 24.33it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1991.60it/s]

Inference: 100%|████████████████

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 17.65it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.62it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1991.60it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.23it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1996.34it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.15it/s]

Tokenization: 100%|█████████████

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 25.25it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 28.89it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1994.44it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.90it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1994.44it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.64it/s]

Tokenization: 100%|█████████████

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.13it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 26.57it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 25.25it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1994.44it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.15it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|████████████████

...

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 25.19it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1994.44it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.05it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1993.49it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.56it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 20.35it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 2010.69it/s]

Inference: 100%|████████████████

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.75it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1995.39it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.93it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 16.35it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 18.82it/s]

Tokenization: 100%|█████████████

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 22.15it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1993.49it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 14.66it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 29.76it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 13.57it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|████████████████

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 15.23it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 19.56it/s]

Tokenization: 100%|████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1995.39it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 13.85it/s]

Tokenization: 100%|██████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<?, ?it/s]

Inference: 100%|█████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 12.87it/s]

Tokenization: 100%|█████████████

MemoryError: Unable to allocate 43.9 GiB for an array with shape (20536, 286749) and data type float64